In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.mplot3d import Axes3D
from random import randint
import matplotlib.cm as cm
import matplotlib.animation as animation

In [ ]:
# 4th Order Runge-Kutta numerical ODE solver
def rk4(f, xvinit, Tmax, N):
    T = np.linspace(0, Tmax, N+1)
    xv = np.zeros( (len(T), len(xvinit)) )
    xv[0] = xvinit
    h = Tmax / N
    for i in range(N):
        k1 = f(xv[i])
        k2 = f(xv[i] + h/2.0*k1)
        k3 = f(xv[i] + h/2.0*k2)
        k4 = f(xv[i] + h*k3)
        xv[i+1] = xv[i] + h/6.0 *( k1 + 2*k2 + 2*k3 + k4)
    return T, xv

In [ ]:
def TSUCS(xvec, a=40, b=55, c=11/6, d=0.16, e=0.65, f=20):
    
    x, y, z = xvec
    dx = a * (y - x) + (d * x * z)
    dy = (b * x) - (x * z) + (f * y)
    dz = - (e * x**2) + (x * y) + (c * z)
    return np.array([dx, dy, dz])

In [ ]:
#  Conditions:

Tmax = 100 # max time value
n = 24000 # steps from 0 to max time
nParticles = 10

In [ ]:
#Create empty dictionaries to store values
d = {} # store position data for each particle
colour = {} # store colour of each particle

In [ ]:
# Generate data and plot it:

fig = plt.figure(figsize=(16,12))
ax = fig.add_subplot(projection='3d')

for i in range(nParticles):
    xrand0 = np.array([randint(-70,70),randint(-70,70),randint(1,70)])
    T, X = rk4(lambda x:TSUCS(xvec = x, a=40, b=55, c=11/6, d=0.16, e=0.65, f=20), xrand0, Tmax, n)
    key = 'particle_' + str(i)
    colourkey = 'colour_' + str(i)
    d[key] = X
    colour[colourkey] = xrand0

    ax.plot([xrand0[0]],[xrand0[1]],[xrand0[2]],'ko')
    ax.plot(X[:,0],X[:,1],X[:,2])
    ax.plot([X[-1,0]],[X[-1,1]],[X[-1,2]], "ro")

plt.show()

In [ ]:
#  Generate the points for the Poincaré maps:

fig_xy = plt.figure(figsize=(16,10))
gs = gridspec.GridSpec(3,3)

ax_xy = fig_xy.add_subplot(gs[2,0])
ax_xy.set_xlabel(r'$x(t)$',fontsize=14)
ax_xy.set_ylabel(r'$y(t)$',fontsize=14)

ax_xz = fig_xy.add_subplot(gs[2,1])
ax_xz.set_xlabel(r'$x(t)$',fontsize=14)
ax_xz.set_ylabel(r'$z(t)$',fontsize=14)

ax_yz = fig_xy.add_subplot(gs[2,2])
ax_yz.set_xlabel(r'$y(t)$',fontsize=14)
ax_yz.set_ylabel(r'$z(t)$',fontsize=14)

z_crossing = 60 # A plane at z = 60, i.e. plot a point every time a particle moves through this plane
y_crossing = 40
x_crossing = 40

# Z=constant P-map point x and y values to plot:
xy_x = [] 
xy_y = []

# X=constant P-map:
xz_x = []
xz_z = []

# X=constant P-map:
yz_y = []
yz_z = []

# Store the colours of the points as they pass through each plane:
colors = cm.get_cmap('rainbow', nParticles+1)
RGBxy = []
RGBxz = []
RGByz = []

# Generating the Poincaré maps and saving the points to plot on each map:
for i in range(1,len(X[:,0])):
    for j in range(nParticles):
        colourkey = 'colour_' + str(j)
        key = 'particle_' + str(j)

        xrand0 = colour[colourkey]
        #print(xrand0)
        X = d[key]
        x_vals = X[:,0]
        y_vals = X[:,1]
        z_vals = X[:,2]
        if (z_vals[i-1] < z_crossing < z_vals[i]) or (z_vals[i-1] > z_crossing > z_vals[i]):
            x = (X[i-1,0] + X[i,0]) / 2
            y = (X[i-1,1] + X[i,1]) / 2

            xy_x.append(x)
            xy_y.append(y)
            RGBxy.append(colors(j))
            ax_xy.scatter(x, y, color=colors(j)[0:3])
        else:
            xy_x.append(0)
            xy_y.append(0)
            RGBxy.append((0,0,0,0))

        if (y_vals[i-1] < y_crossing < y_vals[i]) or (y_vals[i-1] > y_crossing > y_vals[i]):
            x = (X[i-1,0] + X[i,0]) / 2
            z = (X[i-1,2] + X[i,2]) / 2

            xz_x.append(x)
            xz_z.append(z)
            RGBxz.append(colors(j))
            ax_xz.scatter(x, z, color=colors(j)[0:3])
            #print(colors(j))
        else:
            xz_x.append(0)
            xz_z.append(0)
            RGBxz.append((0,0,0,0))

        if (x_vals[i-1] < x_crossing < x_vals[i]) or (x_vals[i-1] > x_crossing > x_vals[i]):
            y = (X[i-1,1] + X[i,1]) / 2
            z = (X[i-1,2] + X[i,2]) / 2

            yz_y.append(y)
            yz_z.append(z)
            RGByz.append(colors(j))
            ax_yz.scatter(y, z, color=colors(j)[0:3])
        else:
            yz_y.append(0)
            yz_z.append(0)
            RGByz.append((0,0,0,0))
#print(len(xy_x))
plt.show()

In [ ]:
# Produce a list that contains the colours used for the particles
line_col = []
for i in range(nParticles):
    s = colors(i)
    k=0
    k = '#%02x%02x%02x' % (int(s[0] * 255), int(s[1] * 255), int(s[2] * 255))
    line_col.append(k)
#print(line_col)

In [ ]:
#  Limits for the plots
xlim_xy = ax_xy.get_xlim()
xlim_xz = ax_xz.get_xlim()
xlim_yz = ax_yz.get_xlim()

ylim_xy = ax_xy.get_ylim()
ylim_xz = ax_xz.get_ylim()
ylim_yz = ax_yz.get_ylim()

In [ ]:
#  Write a function to generate the animation:
#  Note that FuncAnimation did not work on Windows 10 laptop. 
# Instead I saved each image then used Windows in-built video creator tool to create a video from the images.
# You can try FuncAnimation - uncomment the relevant code in subsequent cells.

gs = gridspec.GridSpec(4,3)
def animator(n, index): # inputs a list with index [i] and [i+1] being the time steps to plot between. Below for example
    fig3 = plt.figure(figsize=(12,16))
    for f in range(n[index],int(n[index + 1])):
        print('f=', f)
        plt.close(fig3)
        fig3 = plt.figure(figsize=(12,16))
        plt.tight_layout

        ax3 = fig3.add_subplot(gs[0:3,0:3],projection='3d')
        ax3.set_xlim(-175, 140)
        ax3.set_ylim(-150, 225)
        ax3.set_zlim(-25, 230)
        ax3.view_init(elev=0.,azim=-30)
        ax3.set_axis_off()

        ax_xy = fig3.add_subplot(gs[3,0])
        ax_xy.set_xlim(xlim_xy)
        ax_xy.set_ylim(ylim_xy)
        ax_xy.set_xlabel(r'$x(t)$',fontsize=14)
        ax_xy.set_ylabel(r'$y(t)$',fontsize=14)

        ax_xz = fig3.add_subplot(gs[3,1])
        ax_xz.set_xlim(xlim_xz)
        ax_xz.set_ylim(ylim_xz)
        ax_xz.set_xlabel(r'$x(t)$',fontsize=14)
        ax_xz.set_ylabel(r'$z(t)$',fontsize=14)

        ax_yz = fig3.add_subplot(gs[3,2])
        ax_yz.set_xlim(xlim_yz)
        ax_yz.set_ylim(ylim_yz)
        ax_yz.set_xlabel(r'$y(t)$',fontsize=14)
        ax_yz.set_ylabel(r'$z(t)$',fontsize=14)

        for i in range(nParticles):
            colourkey = 'colour_' + str(i)
            key = 'particle_' + str(i)

            xrand0 = colour[colourkey]
            X = d[key]

            ax3.plot([xrand0[0]],[xrand0[1]],[xrand0[2]],'ko')
            ax3.plot([X[f,0]],[X[f,1]],[X[f,2]], "o", color=line_col[i])
            ax_xy.scatter(xy_x[0:(10*f)],xy_y[0:(10*f)],c =RGBxy[0:(10*f)])
            ax_xz.scatter(xz_x[0:(10*f)],xz_z[0:(10*f)],c=RGBxz[0:(10*f)])
            ax_yz.scatter(yz_y[0:(10*f)],yz_z[0:(10*f)],c=RGByz[0:(10*f)])
            if f < 401: 
                if f < 2:
                    ax3.plot(X[0:f+1,0],X[0:f+1,1],X[0:f+1,2], lw=1.5, color=colors(i))
                else:   #  add a chunky line behind the particle to make it more visible
                    streak = f - 3
                    ax3.plot(X[0:streak+1,0],X[0:streak+1,1],X[0:streak+1,2], lw=1, color=colors(i))
                    ax3.plot(X[streak:f+1,0],X[streak:f+1,1],X[streak:f+1,2], lw=5, color=colors(i))
                    
            else: # this adds variable line thickness to the traced-out paths, depending on the distance traced out.
                g = f - 400
                streak = f - 3
                ax3.plot(X[0:g+1,0],X[0:g+1,1],X[0:g+1,2], lw=0.2, color=colors(i))
                ax3.plot(X[g:streak+1,0],X[g:streak+1,1],X[g:streak+1,2], lw=1, color=colors(i))
                ax3.plot(X[streak:f+1,0],X[streak:f+1,1],X[streak:f+1,2], lw=5, color=colors(i))
        fig3.savefig('$PATH TO FOLDER$/TSUCS_%s.png' %(f)) # add path to the folder where you will save the images

In [ ]:
#  Run this if you have FuncAnimation working on your laptop, it doesn't work on mine.
#animation = animation.FuncAnimation(fig3, animator, interval = 20, blit = True)

# minor ammendments may be required

In [ ]:
# Run the animator function. I split it up into chunks because my computer couldn't handle doing all the iterations in
# a single run; it needed a break.
n_list = [0,250,500,750,1000,1250,1500]
animator(n_list, 0)

In [ ]:
# Store for future use if you so wish:

%store X
%store RGBxy
%store RGBxz
%store RGByz
%store xrand0
%store colour
%store d
%store xy_x  
%store xy_y 
%store xz_x  
%store xz_z  
%store yz_y  
%store yz_z  
%store colors 
%store line_col
%store xlim_xy
%store xlim_xz
%store xlim_yz
%store ylim_xy
%store ylim_xz
%store ylim_yz

In [ ]:
# Execute this to return all your saved/stored values:
%store -r